#  Cadences in a Corpus

### What Can You Do with this NB?

Here we assemble various methods for finding, sorting, grouping cadences in several pieces at once.

Refer to the Corpus Notebook to learn more about corpus methods.



## A. Import Intervals and Other Code


In [1]:
import intervals
from intervals import * 
from intervals import main_objs
import intervals.visualizations as viz
import pandas as pd
import re
import altair as alt 
from ipywidgets import interact
from pandas.io.json import json_normalize
from pyvis.network import Network
from IPython.display import display
import requests
import os
import glob as glob

MYDIR = ("saved_csv")
CHECK_FOLDER = os.path.isdir(MYDIR)

# If folder doesn't exist, then create it.
if not CHECK_FOLDER:
    os.makedirs(MYDIR)
    print("created folder : ", MYDIR)
else:
    print(MYDIR, "folder already exists.")
    
MUSDIR = ("Music_Files")
CHECK_FOLDER = os.path.isdir(MUSDIR)

# If folder doesn't exist, then create it.
if not CHECK_FOLDER:
    os.makedirs(MUSDIR)
    print("created folder : ", MUSDIR)
else:
    print(MUSDIR, "folder already exists.")

saved_csv folder already exists.
Music_Files folder already exists.


## B. Importing Corpus

One method:

* The pieces are provided as a **list**, within square brackets and separated by commas.  
* Complete URLs of each piece in this case
* The bracketed list is then contained within the parentheses of `CorpusBase()`
* For example: 

```
corpus CorpusBase(['https://crimproject.org/mei/CRIM_Mass_0006_1.mei', 'https://crimproject.org/mei/CRIM_Mass_0006_2.mei', 'https://crimproject.org/mei/CRIM_Mass_0006_3.mei'])
```
    
Another method:

* Simply load **all** the pieces in the local `Music_Files/` folder:

```
piece_list = []
for name in glob.glob('Music_Files/*'):
    piece_list.append(name)
piece_list
```

Read the documentation:  `print(CorpusBase.batch.__doc__)`


### Full CRIM Corpus

* Here we omit various monophonic pieces and a few others for which there are errors.

```
piece_list = []
raw_prefix = "https://raw.githubusercontent.com/CRIM-Project/CRIM-online/master/crim/static/mei/MEI_4.0/"
URL = "https://api.github.com/repos/CRIM-Project/CRIM-online/git/trees/990f5eb3ff1e9623711514d6609da4076257816c"
piece_json = requests.get(URL).json()
```

* A list of files to exclude:

```
exclude_list = ['CRIM_Model_0003.mei', 'CRIM_Model_0004.mei', 'CRIM_Model_0005.mei', 'CRIM_Model_0006.mei', 'CRIM_Model_0007.mei','CRIM_Model_0022.mei', 'CRIM_Model_0028.mei', 'CRIM_Model_0035.mei', 'CRIM_Mass_0029_4.mei', 'CRIM_Mass_0049_2.mei','CRIM_Mass_0049_5.mei']
```

*  The following ensures that we don't try to analyze the 'Mass head only' files, which have no musical content:

```
pattern = 'CRIM_Mass_([0-9]{4}).mei
```

* Now the request for all the files


```for p in piece_json["tree"]:
p_name = p["path"]
if re.search(pattern, p_name):
    pass
elif p_name in exclude_list:
    pass
else:
    piece_list.append(raw_prefix + p["path"])
```

In [5]:
# this will pull ALL pieces from CRIM on Github
# Note that we exclude various monophonic pieces (which have no contrapuntal cadences)
# and also a few pieces that seem to throw errors for reasons we don't understand.
corpus_list = []
raw_prefix = "https://raw.githubusercontent.com/CRIM-Project/CRIM-online/master/crim/static/mei/MEI_4.0/"
URL = "https://api.github.com/repos/CRIM-Project/CRIM-online/git/trees/990f5eb3ff1e9623711514d6609da4076257816c"
piece_json = requests.get(URL).json()

# list of files to exclude
exclude_list = ['CRIM_Model_0003.mei', 'CRIM_Model_0004.mei', 'CRIM_Model_0005.mei', 'CRIM_Model_0006.mei', 
             'CRIM_Model_0007.mei',
            'CRIM_Model_0022.mei', 'CRIM_Model_0028.mei', 'CRIM_Model_0035.mei', 'CRIM_Mass_0029_4.mei', 
             'CRIM_Mass_0049_2.mei',
            'CRIM_Mass_0049_5.mei']

# this ensures that we don't try to analyze the 'Mass head only' files, which have no musical content

pattern = 'CRIM_Mass_([0-9]{4}).mei'

# and now the request for all the files
for p in piece_json["tree"]:
    p_name = p["path"]
    if re.search(pattern, p_name):
        pass
    elif p_name in exclude_list:
        pass
    else:
        corpus_list.append(raw_prefix + p["path"])

In [6]:
# To shorten that corpus:

corpus_list = [05]

SyntaxError: invalid syntax (1223302510.py, line 3)

In [ ]:
corpus  = CorpusBase(corpus_list)
corpus

Error downloading https://raw.githubusercontent.com/CRIM-Project/CRIM-online/master/crim/static/mei/MEI_4.0/CRIM_Mass_0004_3.mei, please check your url and try again. Continuing to next file.


In [2]:
# use this to make a list of all the pieces in the Music_Files folder

corpus_list = []
for name in glob.glob('Music_Files/*'):
    corpus_list.append(name)
#     print(name)
corpus = CorpusBase(corpus_list)

In [8]:
# Run this to check for files that fail to process

corpus.batch(func=ImportedPiece.cadences, verbose=True)    


Running cadences analysis on 3 pieces:
	1: Missa Confitemini: Kyrie
	2: Missa Confitemini: Gloria
	3: Missa Confitemini: Credo


[             CadType  LeadingTones CVFs  Low RelLow Tone RelTone  TSig  \
 28.0   Clausula Vera             0   CT   D3    -P4    D      P5   4/2   
 40.0       Authentic             0  TCB   D3    -P4    D      P5   4/2   
 56.0       Authentic             0   CB  B-3     m3    D      P5   4/2   
 72.0       Authentic             1  CTB   G3     P1    G      P8   8/2   
 128.0      Authentic             0   CB   G3     P1    G      P8   4/2   
 136.0  Clausula Vera             0   TC   G3     P1    G      P8   4/2   
 144.0      Authentic             0  CTB   D3    -P4    D      P5   4/2   
 192.0  Clausula Vera             1   CT   G3     P1    G      P8   4/2   
 208.0  Clausula Vera             0   TC   G3     P1    G      P8   4/2   
 236.0      Authentic             1  CTB   G3     P1    G      P8  10/2   
 
        Measure  Beat  Sounding  Progress  SinceLast  ToNext      Composer  \
 28.0         4   3.0       4.0  0.118644       28.0    12.0  Pierre Colin   
 40.0         6  

### C. 1 Find the Cadences in the Corpus

* Sample code (remember to omit "()" after the cadences function!


```
func = ImportedPiece.cadences
list_of_dfs = corpus.batch(func=func, metadata=True)
combined_df = pd.concat(list_of_dfs, ignore_index=False)
```

* Suggested reorganization of columns in the output:

```
col_list = ['Composer', 'Title', 'Measure', 'Beat', 'CadType', 'Tone','Evaded', 'LeadingTones', 'Low','RelLow','RelTone','Progress','SinceLast','ToNext', 'Validation', 'Comments']
combined_df = combined_df[col_list]
```

In [3]:
func = ImportedPiece.cadences
list_of_dfs = corpus.batch(func=func, kwargs={'keep_keys': True}, metadata=True)
combined_df = pd.concat(list_of_dfs, ignore_index=False)

# new order for columns:
col_list = ['Composer', 'Title', 'Measure', 'Beat', 'Pattern', 'Key', 'CadType', 'Tone','CVFs',
                'LeadingTones', 'Sounding', 'Low','RelLow','RelTone',
                'Progress','SinceLast','ToNext']
combined_df = combined_df[col_list]


In [4]:
combined_df.to_csv("morley_corpus_Morgan_Method.csv")

Composer            Title  Measure  Beat  Pattern  \
52.0              Morley  Morley_1597_068        7   3.0      BC1   
76.0              Morley  Morley_1597_068       10   3.0      BC1   
96.0              Morley  Morley_1597_068       13   1.0      BC1   
104.0             Morley  Morley_1597_068       14   1.0    C1T-2   
112.0             Morley  Morley_1597_068       15   1.0    C2T-2   
116.0             Morley  Morley_1597_068       15   3.0    C1T-2   
134.0             Morley  Morley_1597_068       18   1.0      BC1   
188.0   Josquin Des Prés        Ave Maria       24   3.0      C1b   
232.0   Josquin Des Prés        Ave Maria       30   1.0      C1b   
272.0   Josquin Des Prés        Ave Maria       35   1.0    C2T-1   
304.0   Josquin Des Prés        Ave Maria       39   1.0  A2C2T-1   
416.0   Josquin Des Prés        Ave Maria       53   1.0      BC1   
472.0   Josquin Des Prés        Ave Maria       60   1.0      BC1   
512.0   Josquin Des Prés        Ave Maria       65   1.0    C1T-2   
608.0   Josquin Des Prés        Ave Maria       77   1.0      BC1   
640.0   Josquin Des Prés        Ave Maria       81   1.0    C1T-2   
664.0   Josquin Des Prés        Ave Maria       84   1.0    C1T-2   
688.0   Josquin Des Prés        Ave Maria       87   1.0    C2T-1   
736.0   Josquin Des Prés        Ave Maria       93   1.0    C1T-2   
928.0   Josquin Des Prés        Ave Maria      109   1.0      BC1   
1008.0  Josquin Des Prés        Ave Maria      119   1.0    C1T-2   
1072.0  Josquin Des Prés        Ave Maria      127   1.0    C1T-2   
1096.0  Josquin Des Prés        Ave Maria      130   1.0      A1b   
1184.0  Josquin Des Prés        Ave Maria      141   1.0    A2T-2   

                          Key                 CadType Tone  CVFs  \
52.0            ^BC(1|3)x?z?$               Authentic    G   TCB   
76.0            ^BC(1|3)x?z?$               Authentic    G   tCB   
96.0            ^BC(1|3)x?z?$               Authentic    A   TCB   
104.0         ^C(1|3)T-2x?z?$           Clausula Vera    G    CT   
112.0         ^C(2|4)T-2x?z?$           Clausula Vera    D    CT   
116.0         ^C(1|3)T-2x?z?$           Clausula Vera    G    CT   
134.0           ^BC(1|3)x?z?$               Authentic    G   TCB   
188.0               ^C(1|3)b$        Evaded Authentic    G   TCb   
232.0               ^C(1|3)b$        Evaded Authentic    C  CuTb   
272.0         ^C(2|3|4)T-1z?$  Phrygian Clausula Vera    E    CT   
304.0   ^A(2|3)C(2|3|4)T-1z?$  Phrygian Clausula Vera    E   ACT   
416.0           ^BC(1|3)x?z?$               Authentic    C   CTB   
472.0           ^BC(1|3)x?z?$               Authentic    C   CTB   
512.0         ^C(1|3)T-2x?z?$           Clausula Vera    C   tCT   
608.0           ^BC(1|3)x?z?$               Authentic    C   CTB   
640.0         ^C(1|3)T-2x?z?$           Clausula Vera    G    TC   
664.0         ^C(1|3)T-2x?z?$           Clausula Vera    G    TC   
688.0         ^C(2|3|4)T-1z?$  Phrygian Clausula Vera    E    TC   
736.0         ^C(1|3)T-2x?z?$           Clausula Vera    C    CT   
928.0           ^BC(1|3)x?z?$               Authentic    C   CTB   
1008.0        ^C(1|3)T-2x?z?$           Clausula Vera    G    TC   
1072.0        ^C(1|3)T-2x?z?$           Clausula Vera    G    TC   
1096.0      ^A(1|2|3|4)bx?z?$           Altizans Only    C   AbT   
1184.0      ^A(2|4)T-2x?y?z?$           Altizans Only    G    AT   

        LeadingTones  Sounding Low RelLow RelTone  Progress  SinceLast  ToNext  
52.0               1       3.0  G3     P1      P8  0.388060       52.0    24.0  
76.0               1       3.0  G3     P1      P8  0.567164       24.0    20.0  
96.0               1       3.0  A3     M2      M2  0.716418       20.0     8.0  
104.0              1       3.0  G3     P1      P8  0.776119        8.0     8.0  
112.0              0       3.0  D4     P5      P5  0.835821        8.0     4.0  
116.0              1       3.0  B3     M3      P8  0.865672        4.0    18.0  
134.0              1  

### C.2.  Summarize by Type, Tone, etc

* Here you can report an inventory of cadences by **type** and **tone** (and **evaded** status):

```
combined_df['Tone'].value_counts().to_frame()
```




In [12]:
combined_df['CadType'].value_counts().to_frame()


CadType
Clausula Vera                 59
Authentic                     35
Phrygian Clausula Vera        22
Evaded Authentic              12
Phrygian                       6
Abandoned Authentic            6
Evaded Clausula Vera           4
Abandoned Clausula Vera        2
Altizans Only                  2

* Or, various groupings:


>`combined_df.groupby(['CadType', 'Tone', 'Evaded']).size().reset_index(name='counts')`

In [13]:

grouped_types = combined_df.groupby(['Sounding', 'CVFs', 'Tone', 'CadType']).size().reset_index(name='counts')
grouped_types

Sounding CVFs Tone                  CadType  counts
0        1.0   CT   B-            Clausula Vera       1
1        2.0   CB    F                Authentic       1
2        2.0   CB    G                Authentic       1
3        2.0   CT    A   Phrygian Clausula Vera       2
4        2.0   CT   B-            Clausula Vera       5
..       ...  ...  ...                      ...     ...
64       4.0  TCx    G            Clausula Vera       1
65       4.0  tCB    C                Authentic       1
66       4.0  tCB    G                Authentic       2
67       4.0  tCT    G            Clausula Vera       1
68       4.0   zC    G  Abandoned Clausula Vera       2

[69 rows x 5 columns]

### D. Corpus Cadences with Verovio Rendering

```
func = ImportedPiece.verovioCadences
corpus.batch(func=func)
```

Or for local files

```

for name in glob.glob('Music_Files/*'):
    piece = importScore(name)
    piece.verovioCadences()
```

In [13]:
func = ImportedPiece.verovioCadences
corpus.batch(func=func)

Results:
File Name:  CRIM_Mass_0001_1
Pierre Colin
Missa Confitemini: Kyrie
Cadence End Measure: 4
Beat:  3.0
Cadence Tone:  D
Cadence Type:  Clausula Vera
Cadential Voice Functions:  CT


[Warning] Unsupported data.PERCENT '100'
[Warning] Unsupported data.PERCENT '100'
[Warning] Unsupported data.PERCENT '100'
[Warning] Unsupported data.PERCENT '100'
[Warning] Unsupported '<line>' within <measure>
[Warning] Unsupported '<line>' within <measure>


Results:
File Name:  CRIM_Mass_0001_1
Pierre Colin
Missa Confitemini: Kyrie
Cadence End Measure: 6
Beat:  1.0
Cadence Tone:  D
Cadence Type:  Authentic
Cadential Voice Functions:  TCB


Results:
File Name:  CRIM_Mass_0001_1
Pierre Colin
Missa Confitemini: Kyrie
Cadence End Measure: 8
Beat:  1.0
Cadence Tone:  D
Cadence Type:  Authentic
Cadential Voice Functions:  CB


Results:
File Name:  CRIM_Mass_0001_1
Pierre Colin
Missa Confitemini: Kyrie
Cadence End Measure: 10
Beat:  1.0
Cadence Tone:  G
Cadence Type:  Authentic
Cadential Voice Functions:  CTB


...

Results:
File Name:  CRIM_Mass_0001_1
Pierre Colin
Missa Confitemini: Kyrie
Cadence End Measure: 18
Beat:  1.0
Cadence Tone:  D
Cadence Type:  Authentic
Cadential Voice Functions:  CTB


Results:
File Name:  CRIM_Mass_0001_1
Pierre Colin
Missa Confitemini: Kyrie
Cadence End Measure: 23
Beat:  1.0
Cadence Tone:  G
Cadence Type:  Clausula Vera
Cadential Voice Functions:  CT


Results:
File Name:  CRIM_Mass_0001_1
Pierre Colin
Missa Confitemini: Kyrie
Cadence End Measure: 25
Beat:  1.0
Cadence Tone:  G
Cadence Type:  Clausula Vera
Cadential Voice Functions:  TC


Results:
File Name:  CRIM_Mass_0001_1
Pierre Colin
Missa Confitemini: Kyrie
Cadence End Measure: 28
Beat:  3.0
Cadence Tone:  G
Cadence Type:  Authentic
Cadential Voice Functions:  CTB


AttributeError: 'NoneType' object has no attribute 'columns'

In [14]:

for name in glob.glob('Music_Files/*'):
    piece = importScore(name)
    piece.verovioCadences()

Successfully imported Music_Files/CRIM_Mass_0033_4 copy.mei


[Warning] Unsupported data.PERCENT '100'
[Warning] Unsupported data.PERCENT '100'
[Warning] Unsupported data.PERCENT '100'
[Warning] Unsupported data.PERCENT '100'
[Warning] 3 time pointing element(s) could not be matched in measure m-2726
[Warning] 4 time pointing element(s) could not be matched in measure m-1895
[Warning] 4 time pointing element(s) could not be matched in measure m-1211
[Warning] 4 time pointing element(s) could not be matched in measure m-774


Results:
File Name:  CRIM_Mass_0033_4 copy
Roland de Lassus
Missa Doulce memoire: Sanctus
Cadence End Measure: 6
Beat:  1.0
Cadence Tone:  A
Cadence Type:  Authentic
Cadential Voice Functions:  CuTB


Results:
File Name:  CRIM_Mass_0033_4 copy
Roland de Lassus
Missa Doulce memoire: Sanctus
Cadence End Measure: 14
Beat:  1.0
Cadence Tone:  A
Cadence Type:  Clausula Vera
Cadential Voice Functions:  CT


Results:
File Name:  CRIM_Mass_0033_4 copy
Roland de Lassus
Missa Doulce memoire: Sanctus
Cadence End Measure: 19
Beat:  1.0
Cadence Tone:  A
Cadence Type:  Clausula Vera
Cadential Voice Functions:  CT


...

Results:
File Name:  Conseil_Adjuva
Jean Conseil
Copied from Psalmorum Selectorum, Liber 4
(Nürnberg: Johann vom Berg & Ulrich Neuber, 1554)
Adiuva me Domine
Cadence End Measure: 84
Beat:  3.0
Cadence Tone:  D
Cadence Type:  Clausula Vera
Cadential Voice Functions:  CT


Results:
File Name:  Conseil_Adjuva
Jean Conseil
Copied from Psalmorum Selectorum, Liber 4
(Nürnberg: Johann vom Berg & Ulrich Neuber, 1554)
Adiuva me Domine
Cadence End Measure: 87
Beat:  3.0
Cadence Tone:  D
Cadence Type:  Authentic
Cadential Voice Functions:  CuTB


Results:
File Name:  Conseil_Adjuva
Jean Conseil
Copied from Psalmorum Selectorum, Liber 4
(Nürnberg: Johann vom Berg & Ulrich Neuber, 1554)
Adiuva me Domine
Cadence End Measure: 95
Beat:  3.0
Cadence Tone:  G
Cadence Type:  Authentic
Cadential Voice Functions:  CTB


Results:
File Name:  Conseil_Adjuva
Jean Conseil
Copied from Psalmorum Selectorum, Liber 4
(Nürnberg: Johann vom Berg & Ulrich Neuber, 1554)
Adiuva me Domine
Cadence End Measure: 103
Beat:  3.0
Cadence Tone:  G
Cadence Type:  Authentic
Cadential Voice Functions:  CTB


Results:
File Name:  Conseil_Adjuva
Jean Conseil
Copied from Psalmorum Selectorum, Liber 4
(Nürnberg: Johann vom Berg & Ulrich Neuber, 1554)
Adiuva me Domine
Cadence End Measure: 113
Beat:  1.0
Cadence Tone:  G
Cadence Type:  Authentic
Cadential Voice Functions:  CuTB
